In [1]:
#%run basket_RF.ipynb

In [1]:
import pandas as pd
import numpy as np
import datetime as dt
from pathlib import Path
from datetime import datetime, timedelta
from dotenv import load_dotenv
import os
import requests
import matplotlib.pyplot as plt
import hvplot.pandas
%matplotlib inline
import panel as pn
from panel.interact import interact
import plotly.express as px
from phantomjs import Phantom

import warnings
warnings.filterwarnings('ignore')

In [2]:
#ANALYSIS: 

#import RF portfolio and benchmark currency basket
Results = pd.read_pickle('RF_portfolio_results.pickle')
benchmark_df = pd.read_pickle('benchmark_df.pickle')

#rename columns and resize to match RF predicted sample size

benchmark_df = benchmark_df.loc[Results.index[0]:]
benchmark_df = benchmark_df.dropna()

#calculate basket daily return and shift dataframe
daily_returns = benchmark_df.pct_change().shift(-1)

#define porfolio daily returns and dropNA
daily_returns['portfolio'] = (Results['Portfolio Forward Daily Returns'] * Results['RF Predicted Value'])
daily_returns = daily_returns.dropna()

In [3]:
#calculate daily return and moving average of daily return volatility
window = 50

for currency in daily_returns:
    daily_returns[f'{currency} return'] = (1 + daily_returns[{currency}]).cumprod()
    daily_returns[f'{currency} Vol'] = daily_returns[{currency}].rolling(window = window).std()

daily_returns = daily_returns.dropna()

#calculate rolling beta of portfolio to currencies

for currency in daily_returns.iloc[:,:3]:
    daily_returns[f'portfolio to {currency} cov'] = daily_returns['portfolio return'].rolling(window= window).cov(daily_returns[{currency}])
    daily_returns[f'portfolio to {currency} var'] = daily_returns['portfolio return'].rolling(window=window).var()  
    daily_returns[f'portfolio to {currency} beta'] = daily_returns[f'portfolio to {currency} cov']/daily_returns[f'portfolio to {currency} var']

#drop na and fill any inf/-inf values with the previous value
#daily_returns = daily_returns.dropna()
daily_returns = daily_returns.replace(to_replace = np.NaN, method = 'ffill')
daily_returns = daily_returns.replace(to_replace = np.inf, method = 'ffill')
daily_returns = daily_returns.replace(to_replace =-np.inf, method = 'ffill')
daily_returns

FRED/DEXUSEU  FRED/DEXCAUS  ECB/EURCHF  portfolio  \
Date                                                            
2006-08-31      0.003127     -0.000904    0.002540  -0.000559   
2006-09-01     -0.001792      0.004975    0.001140  -0.000559   
2006-09-05     -0.001795     -0.005310    0.002214   0.000068   
2006-09-06     -0.002346      0.004253   -0.001389  -0.001325   
2006-09-07     -0.006585      0.008289   -0.000316  -0.001025   
...                  ...           ...         ...        ...   
2021-02-18      0.004802     -0.008657    0.002032   0.001199   
2021-02-19      0.001566      0.000794    0.003410   0.001256   
2021-02-22     -0.001070      0.000317    0.005327  -0.000046   
2021-02-23      0.007165     -0.006503    0.011876  -0.000046   
2021-02-25     -0.011121      0.013570   -0.008126   0.000010   

            FRED/DEXUSEU return  FRED/DEXUSEU Vol  FRED/DEXCAUS return  \
Date                                                                     
2006-08-31             1.014535          0.005237             1.002169   
2006-09-01             1.012716          0.005152             1.007155   
2006-09-05             1.010898          0.005109             1.001807   
2006-09-06             1.008526          0.005114             1.006067   
2006-09-07             1.001886          0.005195             1.014406   
...                         ...               ...                  ...   
2021-02-18             0.972585          0.003072             1.135953   
2021-02-19             0.974108          0.003078             1.136855   
2021-02-22             0.973066          0.003082             1.137215   
2021-02-23             0.980038          0.003225             1.129820   
2021-02-25             0.969139          0.003582             1.145152   

            FRED/DEXCAUS Vol  ECB/EURCHF return  ECB/EURCHF Vol  ...  \
Date                                                             ...   
2006-08-31          0.004197           1.012872        0.001423  ...   
2006-09-01          0.003892           1.014026        0.001423  ...   
2006-09-05          0.003863           1.016271        0.001450  ...   
2006-09-06          0.003916           1.014860        0.001464  ...   
2006-09-07          0.004079           1.014539        0.001435  ...   
...                      ...                ...             ...  ...   
2021-02-18          0.003935           0.702847        0.001730  ...   
2021-02-19          0.003854           0.705244        0.001789  ...   
2021-02-22          0.003855           0.709000        0.001911  ...   
2021-02-23          0.003949           0.717421        0.002495  ...   
2021-02-25          0.004415           0.711591        0.002766  ...   

            portfolio Vol  portfolio to FRED/DEXUSEU cov  \
Date                                                       
2006-08-31       0.001017                            NaN   
2006-09-01       0.001015                            NaN   
2006-09-05       0.001015                            NaN   
2006-09-06       0.001025                            NaN   
2006-09-07       0.001034                            NaN   
...                   ...                            ...   
2021-02-18       0.000931                  -6.909337e-08   
2021-02-19       0.000893                   1.894098e-08   
2021-02-22       0.000893                  -1.238471e-07   
2021-02-23       0.000880                   2.771788e-07   
2021-02-25       0.000880                  -1.073163e-06   

            portfolio to FRED/DEXUSEU var  portfolio to FRED/DEXUSEU beta  \
Date                                                                        
2006-08-31                            NaN                             NaN   
2006-09-01                            NaN                             NaN   
2006-09-05                            NaN                             NaN   
2006-09-06                            NaN                             NaN   
2006-09-07             

In [4]:
#plot daily prices of this year
year = "2020"
daily_price_plot = benchmark_df.loc[year:].hvplot(
    kind = 'line',
    size = 70,
    width = 800,
    height = 400,
    label = "Daily Price"
)
daily_price_plot = daily_price_plot * Results.loc[year:,'Portfolio Adjusted Close'].hvplot(kind = 'line')
daily_price_plot

:Overlay
   .NdOverlay.Daily_Price          :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Curve.Portfolio_Adjusted_Close :Curve   [Date]   (Portfolio Adjusted Close)

In [5]:
# Calculate cumulative return of model and plot equity curve against the benchmark currency basket curves (individual and combined)
return_curve = daily_returns.loc[:, daily_returns.columns.str.endswith('return')]
return_curve['Combined benchmark Return'] = return_curve.iloc[:, 1:].mean(axis=1)
return_curve_plot = return_curve.hvplot(
    kind = 'line',
    size = 70,
    width = 800,
    height = 400,
    label = "Portfolio vs Benchmark Currency Return"
)
return_curve_plot

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [6]:
# group beta and Volatility dataframes for analysis
beta= daily_returns.loc[:,  daily_returns.columns.str.endswith("beta")]
beta['Combined Benchmark Beta'] = beta.iloc[:, :3].mean(axis = 1)

#plot rolling betas against benchmark currency basket
beta_plot = beta.hvplot(
    kind = 'line',
    size =70,
    width = 800,
    label = 'Portfolio Vol Graph: Benchmark Currency Basket Beta'
)
beta_plot

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [7]:
#calculate % of time beta is between 1 and -1 and also within 1/2 std deviation of zero to compare portfolio volatility characteristics, display message
nl = '\n'

daily_Vol_average = daily_returns.iloc[:, :4].mean()
beta_std = beta.std()
beta_mean = beta.mean()
days_of_low_vol = beta[(beta < 1) & (beta > -1)].count()/beta.count()
days_of_extreme_low_correlation = beta[(beta < beta_mean + beta_std/4) & (beta > beta_mean - beta_std/4)].count()/beta.count()


print(f'Daily average % change (including weekends):{nl}{daily_Vol_average}{nl}{nl}The percentage of days the portfolio has had low Vol:{nl}{days_of_low_vol} {nl}{nl}The percentage of days the portfolio has had extremely low correlation (beta .5 SD) {nl}{days_of_extreme_low_correlation}{nl}{nl}Total Sample Size{nl}{beta.count()}')


Daily average % change (including weekends):
FRED/DEXUSEU    0.000005
FRED/DEXCAUS    0.000055
ECB/EURCHF     -0.000086
portfolio      -0.000034
dtype: float64

The percentage of days the portfolio has had low Vol:
portfolio to FRED/DEXUSEU beta    0.965986
portfolio to FRED/DEXCAUS beta    0.976474
portfolio to ECB/EURCHF beta      0.994048
Combined Benchmark Beta           0.999433
dtype: float64 

The percentage of days the portfolio has had extremely low correlation (beta .5 SD) 
portfolio to FRED/DEXUSEU beta    0.207200
portfolio to FRED/DEXCAUS beta    0.274943
portfolio to ECB/EURCHF beta      0.363662
Combined Benchmark Beta           0.285431
dtype: float64

Total Sample Size
portfolio to FRED/DEXUSEU beta    3528
portfolio to FRED/DEXCAUS beta    3528
portfolio to ECB/EURCHF beta      3528
Combined Benchmark Beta           3528
dtype: int64


In [46]:
#plot porftolio against benchmark currency basket portfolio
Vol = daily_returns.loc[:, daily_returns.columns.str.endswith('Vol')]
Vol_plot = Vol.hvplot.area(
    size = 70,
    width = 800,
    height = 400,
    stacked = False,
    label = "Daily Return Volatility Comparison",
    ylim = (0, .03)
)
Vol_plot

:NdOverlay   [Variable]
   :Area   [Date]   (value)

In [44]:
#create Vol portfolio of benchmark currency basket
benchmark_Vol = pd.DataFrame()
# combine Vol of currency basket and compare to portfolio
benchmark_Vol['basket Vol'] = Vol.iloc[:, 1:].mean(axis = 1)
benchmark_Vol['portfolio Vol'] = daily_returns['portfolio Vol']

#plot benchmark
benchmark_Vol_plot = benchmark_Vol.hvplot.area(
    y= ['basket Vol', 'portfolio Vol'],
    stacked = False,
    legend = 'top_right',
    width = 800,
    height = 400,
    label = "Portfolio vs Benchmark Daily Return Vol",
    ylim = (0, .02)
)
benchmark_Vol_plot

:NdOverlay   [Variable]
   :Area   [Date]   (value)

In [18]:
#Analsis since Ethereum was introduced (removing 2008 Financial Crisis as well) Daily Return and Vol graphs
post_ETH = daily_returns.loc["2016":,:"portfolio"]
for currency in post_ETH:
    post_ETH[f'{currency} return'] = (1 + post_ETH[{currency}]).cumprod()
    post_ETH[f'{currency} Vol'] = post_ETH[{currency}].rolling(window = window).std()

return_curve_postETH = post_ETH.loc[: , post_ETH.columns.str.endswith('return')]
return_curve_postETH['Combined benchmark Return'] = return_curve_postETH.iloc[:, :-1].mean(axis=1)
return_curve_postETH_plot = return_curve_postETH.hvplot(
    kind = 'line',
    size = 70,
    width = 800,
    height = 400,
    label = "Portfolio vs Benchmark Currency Return post ETH creation"
)

return_curve_postETH_plot

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [39]:
# plot Portfolio vs Benchmark Vol post ETH
Vol_post_ETH_plot = post_ETH.loc[:, post_ETH.columns.str.endswith('Vol')].hvplot.area(
    size = 70,
    width = 800,
    height = 400,
    stacked = False,
    label = "Daily Return Volatility Comparison post ETH creation",
    ylim = (0, .01)
)
Vol_post_ETH_plot

:NdOverlay   [Variable]
   :Area   [Date]   (value)

In [51]:
return_analysis = pn.Column(return_curve_plot, return_curve_postETH_plot)

In [60]:
Vol_analysis = pn.Column(Vol_plot.opts(shared_axes=False), benchmark_Vol_plot.opts(shared_axes = False), Vol_post_ETH_plot.opts(shared_axes = False))

In [61]:
plots = pn.Tabs(
    ("# Portfolio Return Analysis Dashboard", return_analysis),
    ("# Portfolio Vol Analysis Dashboard", Vol_analysis)
)

In [63]:
plots.servable()

Tabs
    [0] Column
        [0] HoloViews(NdOverlay)
        [1] HoloViews(NdOverlay)
    [1] Column
        [0] HoloViews(NdOverlay)
        [1] HoloViews(NdOverlay)
        [2] HoloViews(NdOverlay)

In [65]:
server = pn.serve(plots, start =True, show = True)

Launching server at http://localhost:57217
